# Анализ поведения пользователей DonorSearch

Задачи:
- Оценить влияние событий из Ленты событий на сайте на количество регистраций и донаций.
- Применить бизнес метрики к анализу данных донаций.
- Дать рекомендации по вопросам: 
    - Как привлекать больше пользователей? 
    - Как вовлекать существующих пользователей?


# Предобработка

In [143]:
# Import libraries
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker
import seaborn as sns
import math as mt
import re
from pandas_profiling import ProfileReport


# Options for pandas
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'
pd.options.display.max_columns = None
pd.options.display.max_colwidth = 300

donations = pd.read_csv('donations_anon.csv') 
plan = pd.read_csv('plan_anon.csv') 
users = pd.read_csv('users_anon.csv') 



In [144]:
[display(i.head(), i.info()) for i in [donations, plan, users]]

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 104770 entries, 0 to 104769
Data columns (total 10 columns):
 #   Column                   Non-Null Count   Dtype 
---  ------                   --------------   ----- 
 0   ID                       104770 non-null  int64 
 1   ID пользователя          104770 non-null  int64 
 2   Класс крови              104770 non-null  object
 3   Дата донации             104770 non-null  object
 4   Дата добавления донации  104770 non-null  object
 5   Тип донации              104770 non-null  object
 6   Регион                   104770 non-null  object
 7   Место стадчи             104770 non-null  object
 8   Статус донации           104770 non-null  object
 9   Есть справка             104770 non-null  object
dtypes: int64(2), object(8)
memory usage: 8.0+ MB


ID  ID пользователя    Класс крови Дата донации  \
0  105346           178983  Цельная кровь   13.11.2021   
1  105345           177352         Плазма   10.12.2021   
2  105344           175382     Тромбоциты   13.12.2021   
3  105343           169669  Цельная кровь   15.12.2021   
4  105342           140960     Тромбоциты   20.11.2020   

  Дата добавления донации   Тип донации  \
0              15.12.2021  Безвозмездно   
1              15.12.2021  Безвозмездно   
2              15.12.2021  Безвозмездно   
3              15.12.2021  Безвозмездно   
4              15.12.2021  Безвозмездно   

                                      Регион Место стадчи Статус донации  \
0                             Россия, Москва          641   На модерации   
1  Россия, Челябинская область, Магнитогорск          587    Без справки   
2                             Россия, Москва          641    Без справки   
3   Россия, Краснодарский край, Новороссийск          138   На модерации   
4                             Россия, Москва          633   На модерации   

  Есть справка  
0           Да  
1          Нет  
2          Нет  
3           Да  
4           Да

None

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4094 entries, 0 to 4093
Data columns (total 9 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   ID                 4094 non-null   int64 
 1   ID пользователя    4094 non-null   int64 
 2   Класс крови        4094 non-null   object
 3   Дата донации       4094 non-null   object
 4   Дата планирования  4094 non-null   object
 5   Тип донации        4094 non-null   object
 6   Регион             4094 non-null   object
 7   Место стадчи       4094 non-null   object
 8   Есть справка       4094 non-null   object
dtypes: int64(2), object(7)
memory usage: 288.0+ KB


ID  ID пользователя    Класс крови Дата донации Дата планирования  \
0  4113           178982  Цельная кровь   25.01.2022        15.12.2021   
1  4112           175382  Цельная кровь   05.01.2022        15.12.2021   
2  4111           178818  Цельная кровь   31.01.2022        15.12.2021   
3  4110           178974  Цельная кровь   25.12.2021        15.12.2021   
4  4109           176064     Тромбоциты   16.12.2021        15.12.2021   

    Тип донации                                  Регион Место стадчи  \
0  Безвозмездно  Россия, Нижегородская область, Арзамас          281   
1  Безвозмездно                          Россия, Москва          641   
2  Безвозмездно                 Россия, Санкт-Петербург          668   
3  Безвозмездно                          Россия, Москва          641   
4  Безвозмездно                          Россия, Москва          633   

            Есть справка  
0  донация запланирована  
1  донация запланирована  
2  донация запланирована  
3  донация запланирована  
4  донация запланирована

None

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 177910 entries, 0 to 177909
Data columns (total 21 columns):
 #   Column                     Non-Null Count   Dtype 
---  ------                     --------------   ----- 
 0   ID                         177910 non-null  int64 
 1   Пол                        177910 non-null  object
 2   Дата рождения              177910 non-null  object
 3   Регион                     177910 non-null  object
 4   Группа крови               177910 non-null  object
 5   Kell-фактор                177910 non-null  object
 6   Цельная кровь              177910 non-null  object
 7   Плазма                     177910 non-null  object
 8   Тромбоциты                 177910 non-null  object
 9   Эритроциты                 177910 non-null  object
 10  Лейкоциты                  177910 non-null  object
 11  Костный мозг               177910 non-null  object
 12  Почетный донор             177910 non-null  object
 13  Отвод от донации           177910 non-null  

ID         Пол Дата рождения          Регион Группа крови  \
0  178985     Женский    03.03.2003      Не указано   Не указано   
1  178984     Мужской    25.01.1981      Не указано   Не указано   
2  178983  Не указано    Не указано  Россия, Москва   B(III) Rh-   
3  178982  Не указано    Не указано      Не указано     O(I) Rh+   
4  178981     Женский    19.06.1995      Не указано   Не указано   

     Kell-фактор Цельная кровь Плазма Тромбоциты Эритроциты Лейкоциты  \
0     Не указано            Да     Да         Да         Да        Да   
1     Не указано            Да     Да         Да         Да        Да   
2  Отрицательный            Да     Да        Нет        Нет       Нет   
3  Положительный            Да     Да         Да         Да        Да   
4     Не указано            Да     Да         Да         Да        Да   

  Костный мозг              Почетный донор Отвод от донации  Цельная кровь.1  \
0          Нет  Дата получения не известна              Нет                0   
1          Нет  Дата получения не известна              Нет                0   
2          Нет  Дата получения не известна              Нет                0   
3          Нет  Дата получения не известна              Нет                0   
4          Нет  Дата получения не известна              Нет                0   

   Плазма.1  Тромбоциты.1  Эритроциты.1  Лейкоциты.1 Дата регистрации  \
0         0             0             0            0       15.12.2021   
1         0             0             0            0       15.12.2021   
2         0             0             0            0       15.12.2021   
3         0             0             0            0       15.12.2021   
4         0             0             0            0       15.12.2021   

   Не подтверждённые донации  
0                          0  
1                          0  
2                          1  
3                          0  
4                          0

None

[None, None, None]

В данных нет явных пропусков, однако не везде правильный тип данных. Также стоит проверить дубликаты и переименовать некоторые столбцы

In [145]:
donations = donations.rename(columns={'Место стадчи': 'Место сдачи'})
plan = plan.rename(columns={'Место стадчи': 'Место сдачи'})


for i in ['Цельная кровь.1', 'Плазма.1', 'Тромбоциты.1', 'Эритроциты.1', 'Лейкоциты.1']:
    users = users.rename(columns={i: i[0:-2] + ', кол.'})

In [146]:
donations['Дата донации'].apply(lambda x: x[-4:]).value_counts()

2015    15729
2016    14477
2014    12632
2018    12604
2017    11097
2019     8986
2021     6727
2020     6328
2013     5860
2012     3347
2011     2290
2010     1576
2009     1064
2008      568
2007      354
2006      268
2005      183
2004      143
2003      131
2002      112
2001       60
2000       57
1999       32
1970       29
1998       18
1990       11
1995       10
1997       10
1988        6
1994        6
1996        6
1989        6
1993        4
1991        4
1992        4
1917        3
1987        3
1920        3
1986        2
1919        2
3013        1
1982        1
2091        1
1985        1
8017        1
.201        1
1918        1
1980        1
3016        1
.214        1
2107        1
.207        1
1971        1
1901        1
.208        1
2050        1
1983        1
1914        1
Name: Дата донации, dtype: int64

Взяв из даты донации год, можно увидеть, что эта величина начинает идти непрерывно только с 1980 года, до этого попадаются случайные даты большой давности, в которые почти не было донаций. Также есть несколько дат из будущего. Все эти даты стоит удалить  

In [147]:
donations['Дата донации'].apply(lambda x: x[-4:]).count()

104770

In [148]:
donations[(donations['Дата донации'].apply(lambda x: x[-4:]) >= '1980') & \
         (donations['Дата донации'].apply(lambda x: x[-4:]) <= '2021')]['Дата донации'].count()

104719

Неверных значений всего 51

In [149]:
donations = donations[(donations['Дата донации'].apply(lambda x: x[-4:]) >= '1980') & \
         (donations['Дата донации'].apply(lambda x: x[-4:]) <= '2021')]

In [150]:
donations['Дата добавления донации'].apply(lambda x: x[-4:]).value_counts()

2020    93015
2021    11704
Name: Дата добавления донации, dtype: int64

В столбце с датой добавления донации все в порядке. Стоит проверить остальные даты в других таблицах

In [151]:
plan['Дата донации'].apply(lambda x: x[-4:]).value_counts()
plan['Дата планирования'].apply(lambda x: x[-4:]).value_counts()

users['Дата рождения'].apply(lambda x: x[-4:]).value_counts()
users['Дата регистрации'].apply(lambda x: x[-4:]).value_counts()

2021    3814
2020     157
2022     123
Name: Дата донации, dtype: int64

2021    3834
2020     260
Name: Дата планирования, dtype: int64

зано    134838
2000      2880
1999      2434
1998      2324
1997      2136
         ...  
1937         1
1075         1
1901         1
2984         1
1885         1
Name: Дата рождения, Length: 137, dtype: int64

2018    133058
2021     23801
2020     16975
2019      4076
Name: Дата регистрации, dtype: int64

Даты в таблице `plan` и столбец `Дата регистрации` в таблице `users` также нормальные, а в столбце `Дата рождения` есть выбросы

In [152]:
temp_list = users['Дата рождения'].apply(lambda x: x[-4:]).value_counts().index.tolist()
sorted(temp_list)

['.200',
 '.998',
 '02.2',
 '05.2',
 '1075',
 '1077',
 '1084',
 '1098',
 '1191',
 '1885',
 '1888',
 '1897',
 '1900',
 '1901',
 '1902',
 '1903',
 '1904',
 '1905',
 '1906',
 '1907',
 '1908',
 '1909',
 '1910',
 '1911',
 '1912',
 '1913',
 '1914',
 '1915',
 '1916',
 '1917',
 '1918',
 '1919',
 '1920',
 '1922',
 '1923',
 '1925',
 '1926',
 '1927',
 '1928',
 '1929',
 '1930',
 '1931',
 '1932',
 '1933',
 '1936',
 '1937',
 '1938',
 '1939',
 '1940',
 '1941',
 '1942',
 '1943',
 '1944',
 '1945',
 '1947',
 '1948',
 '1949',
 '1950',
 '1951',
 '1952',
 '1953',
 '1954',
 '1955',
 '1956',
 '1957',
 '1958',
 '1959',
 '1960',
 '1961',
 '1962',
 '1963',
 '1964',
 '1965',
 '1966',
 '1967',
 '1968',
 '1969',
 '1970',
 '1971',
 '1972',
 '1973',
 '1974',
 '1975',
 '1976',
 '1977',
 '1978',
 '1979',
 '1980',
 '1981',
 '1982',
 '1983',
 '1984',
 '1985',
 '1986',
 '1987',
 '1988',
 '1989',
 '1990',
 '1991',
 '1992',
 '1993',
 '1994',
 '1995',
 '1996',
 '1997',
 '1998',
 '1999',
 '2000',
 '2001',
 '2002',
 '2003',
 

По годам в дате рождения можно оставить даты с 1900 года и до 2020. Также можно заменить знaчение 'не указано' на NaN для приведения столбца к типу datetime

In [153]:
users['Дата рождения'].count()

177910

In [154]:
users[(users['Дата рождения'].str.contains('зано')) | \
      ((users['Дата рождения'].apply(lambda x: x[-4:]) >= '1900') & \
      (users['Дата рождения'].apply(lambda x: x[-4:]) <= '2020'))]['Дата рождения'].count()

177888

Всего 22 выброса

In [155]:
users = users[(users['Дата рождения'].str.contains('зано')) | \
      ((users['Дата рождения'].apply(lambda x: x[-4:]) >= '1900') & \
      (users['Дата рождения'].apply(lambda x: x[-4:]) <= '2020'))]

In [156]:
users.loc[users['Дата рождения'] == 'Не указано', 'Дата рождения'] = np.nan

In [157]:
users.head()

ID         Пол Дата рождения          Регион Группа крови  \
0  178985     Женский    03.03.2003      Не указано   Не указано   
1  178984     Мужской    25.01.1981      Не указано   Не указано   
2  178983  Не указано           NaN  Россия, Москва   B(III) Rh-   
3  178982  Не указано           NaN      Не указано     O(I) Rh+   
4  178981     Женский    19.06.1995      Не указано   Не указано   

     Kell-фактор Цельная кровь Плазма Тромбоциты Эритроциты Лейкоциты  \
0     Не указано            Да     Да         Да         Да        Да   
1     Не указано            Да     Да         Да         Да        Да   
2  Отрицательный            Да     Да        Нет        Нет       Нет   
3  Положительный            Да     Да         Да         Да        Да   
4     Не указано            Да     Да         Да         Да        Да   

  Костный мозг              Почетный донор Отвод от донации  \
0          Нет  Дата получения не известна              Нет   
1          Нет  Дата получения не известна              Нет   
2          Нет  Дата получения не известна              Нет   
3          Нет  Дата получения не известна              Нет   
4          Нет  Дата получения не известна              Нет   

   Цельная кровь, кол.  Плазма, кол.  Тромбоциты, кол.  Эритроциты, кол.  \
0                    0             0                 0                 0   
1                    0             0                 0                 0   
2                    0             0                 0                 0   
3                    0             0                 0                 0   
4                    0             0                 0                 0   

   Лейкоциты, кол. Дата регистрации  Не подтверждённые донации  
0                0       15.12.2021                          0  
1                0       15.12.2021                          0  
2                0       15.12.2021                          1  
3                0       15.12.2021                          0  
4                0       15.12.2021                          0

In [158]:
users['Почетный донор'].apply(lambda x: x[-4:]).value_counts()

стна    170661
2023      3786
2022      2481
2024       746
Да         177
2021        37
Name: Почетный донор, dtype: int64

В столбце `Почетный донор` стоит также преобразовать дату и заменить значения 'Дата получения не известна' и 'Да' на NaN

In [159]:
users.loc[((users['Почетный донор'] == 'Дата получения не известна') | \
           (users['Почетный донор'] == 'Да')), 'Почетный донор'] = np.nan

Теперь во всех таблицах можно привести даты к типу datetime

In [160]:
fmt = '%d.%m.%Y'
donations['Дата донации'] = pd.to_datetime(donations['Дата донации'], format = fmt)
donations['Дата добавления донации'] = pd.to_datetime(donations['Дата добавления донации'], format = fmt)
plan['Дата донации'] = pd.to_datetime(plan['Дата донации'], format = fmt)
plan['Дата планирования'] = pd.to_datetime(plan['Дата планирования'], format = fmt)
users['Дата рождения'] = pd.to_datetime(users['Дата рождения'], format = fmt)
users['Почетный донор'] = pd.to_datetime(users['Почетный донор'], format = fmt)
users['Дата регистрации'] = pd.to_datetime(users['Дата регистрации'], format = fmt)


In [161]:
donations[donations['Дата добавления донации'] < donations['Дата донации']]['Дата добавления донации'].count()
plan[plan['Дата донации'] < plan['Дата планирования']]['Дата планирования'].count()
users[users['Дата регистрации'] < users['Дата рождения']]['Дата рождения'].count()
users[users['Почетный донор'] < users['Дата рождения']]['Дата рождения'].count()
users[users['Почетный донор'] < users['Дата регистрации']]['Дата регистрации'].count()


20

0

39

0

0

Проверив даты можно убедиться, что есть 20 значений, в которых дата донации была после даты добавления донации, и 39 значений, когда дата рождения была после даты регистрации. 

In [162]:
donations = donations[donations['Дата добавления донации'] >= donations['Дата донации']]
users = users[((users['Дата регистрации'] >= users['Дата рождения']) | (users['Дата рождения'].isna()))]


Стоит проверить, нет ли среди доноров несовершеннолетних

In [163]:
temp_df = users.iloc[:, [0, 2, 3, -2]].merge(donations.iloc[:, [1, 3, 6]], how='inner', right_on='ID пользователя', left_on='ID' )
temp_df.sort_values('ID')


ID Дата рождения                                        Регион_x  \
8157        4    1998-07-21                         Россия, Санкт-Петербург   
8156        7    1998-07-03               Россия, Самарская область, Самара   
15407       8    1972-06-24                  Россия, Томская область, Томск   
15408       8    1972-06-24                  Россия, Томская область, Томск   
15409       8    1972-06-24                  Россия, Томская область, Томск   
...       ...           ...                                             ...   
6      178902    1998-12-10            Россия, Воронежская область, Воронеж   
11     178902    1998-12-10            Россия, Воронежская область, Воронеж   
2      178939           NaT  Россия, Нижегородская область, Нижний Новгород   
1      178960    1989-11-14  Россия, Нижегородская область, Нижний Новгород   
0      178983           NaT                                  Россия, Москва   

      Дата регистрации  ID пользователя Дата донации  \
8157        2020-08-18                4   2020-07-08   
8156        2020-08-18                7   2020-08-18   
15407       2020-04-14                8   2020-08-18   
15408       2020-04-14                8   2020-06-16   
15409       2020-04-14                8   2020-04-14   
...                ...              ...          ...   
6           2021-12-14           178902   2021-10-21   
11          2021-12-14           178902   2021-04-29   
2           2021-12-15           178939   2021-12-15   
1           2021-12-15           178960   2021-12-15   
0           2021-12-15           178983   2021-11-13   

                                             Регион_y  
8157                                       Не указано  
8156                                       Не указано  
15407                                      Не указано  
15408                                      Не указано  
15409                                      Не указано  
...                                               ...  
6                Россия, Воронежская область, Воронеж  
11               Россия, Воронежская область, Воронеж  
2      Россия, Нижегородская область, Нижний Новгород  
1      Россия, Нижегородская область, Нижний Новгород  
0                                      Россия, Москва  

[104391 rows x 7 columns]

In [164]:
age18 = 6574 # 18 лет в днях
temp_df[(temp_df['Дата донации'] - temp_df['Дата рождения']).dt.days < age18]['Дата рождения'].count()
len(temp_df[(temp_df['Дата донации'] - temp_df['Дата рождения']).dt.days < age18]['ID'].unique())

246

84

В таблицах есть 246 записей о 84 несовершеннолетних донорах. Кто-то из них сдавали кровь несколько раз, есть вероятность, что нет ошибки и доноры по какой-то причине действительно несовершеннолетние

# Анализ

## Donations

In [165]:
donations_profile = ProfileReport(donations, title = "Donations Profiling Report", explorative=True)
donations_profile


Summarize dataset:   0%|          | 0/24 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

- Все ID - уникальные
- Уникальных ID пользователей около 26%
- Есть 5 классов крови, 69.5% - цельная кровь, 19.5% - плазма
- Даты донаций есть в диапазоне 1980 - 2021 годы, больше всего донаций с 2010 по 2021
- Дата добавления донации имеет всего 0.4% уникальных значений, значит много донаций добавлялись на сайт разом в определенные дни с ноября 2020 по декабрь 2021
- 93% донаций были на безвозмездной основе, остальные - платно
- Более 88% пользователей не указали свой регион, самыми популярными являются: Москва, Казань, Санкт-Петербург
- Около 9% донаций были на выездной акции, самыми популярными местами сдачи были: 633, 176, 641
- 90% донаций приняты, остальные либо без справки, либо удалены, либо отклонены, либо на модерции
- У 97.7% пользователй есть справка, у остальных - нет

## Plan

In [166]:
plan_profile = ProfileReport(plan, title = "Donations Profiling Report", explorative=True)
plan_profile


Summarize dataset:   0%|          | 0/22 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

- Все ID - уникальные
- Уникальных ID уже пользователей 66%
- Те же 5 классов крови, 75.2% - цельная кровь, 15.7% - плазма
- Дата донации имеет около 11% уникальных значений, донации добавляются с ноября 2020 по сентябрь 2022
- Дата планирования имеет 9.4% уникальных значений, донации добавлялись с ноября 2020 по декабрь 2021
- 84% донаций на безвозмездной основе, остальные - платно
- Большинство пользователей указали свой регион, самыми популярными являются: Москва - 26%, Санкт-Петербург - 10%, Казань - 9.3%
- Около 21% донаций планируются на выездной акции
- 46.7% донаций запланированы, 27.4%  запланированных донаций добавлены, остальные планирования отменены


## Users

In [167]:
users_profile = ProfileReport(users, title = "Donations Profiling Report", explorative=True)
users_profile


Summarize dataset:   0%|          | 0/35 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

- Все ID - уникальные
- 74.7% не указали свой пол, женщин чуть больше, чем мужчин
- Дата рождения имеет около 28% уникальных значений, даты находятся в диапазоне 1900 - 2020 годы
- Около 25% не указали свой регион, самыми популярными являются: Москва, Санкт-Петербург, Казань
- Около 90% не указали свою группу крови, самыми распространенными являются: A(II) Rh+, O(I) Rh+, B(III) Rh+
- Около 82% не указали свой Kell-фактор, 8.9% имеют отрицательный, 7.8% - положительный, остальные не знают
- 99.8% сдавали цельную кровь, остальные - нет
- 99.4% сдавали плазму, остальные - нет
- 99.3% сдавали тромбоциты, остальные - нет
- 99.2% сдавали эритроциты, остальные - нет
- 99.1% сдавали лейкоциты, остальные - нет
- 97.4% не сдавали костный мозг
- Звание почетного донора есть или будет у 8.6%, присвоение звания происходит с июня 2021 по ноябрь 2024 года, больше всего присвоений будет в начале 2023 года
- У 99.8% нет отвода от донации
- У 87.9% - 0 цельной крови
- У 97.6% - 0 плазмы
- У 98.7% - 0 тромбоцитов
- У 99.9% - 0 эритроцитов
- У более, чем 99.9% - 0 лейкоцитов
- Регистрации были с апреля 2018 по декабрь 2021 года, причем с мая 2019 по март 2020 года не было регистраций
- У 97.4% - нет неподтвержденных донаций 


In [168]:
# donations.to_csv('donations.csv')
# plan.to_csv('plan.csv')
#users.to_csv('users.csv')

# Tableau

https://public.tableau.com/views/DonorSearch/Story1?:language=en-US&publish=yes&:display_count=n&:origin=viz_share_link

# Presentation

https://docs.google.com/presentation/d/1j27OuhCzYf4ZiX6nR8mmrOFP3xqkzvhTfIa5K3ulKPU/edit?usp=sharing